In [1]:
import sys
sys.path.append("../build/") # my NG-BEM path
from netgen.occ import *
import netgen.meshing as meshing
from ngsolve import *

from libbem import *
from ngsolve import Projector, Preconditioner
from ngsolve.krylovspace import CG

Loading ngbem library


In [2]:
import netgen.gui
from netgen.csg import *

geo = CSGeometry()
sphere = Sphere(Pnt(0,0,0), 1)
geo.Add(sphere.col([0,0,0])) # add spmesh_mulhere
geo.Draw()

Draw(geo)

optfile ./ng.opt does not exist - using default values
togl-version : 2
OCC module loaded


2025-06-10 21:48:12.264 Python[3856:12373568] WARNING: Secure coding is not enabled for restorable state! Enable secure coding by implementing NSApplicationDelegate.applicationSupportsSecureRestorableState: and returning YES.


loading ngsolve library
NGSolve-6.2.2403
Using Lapack
Including sparse direct solver UMFPACK
Running parallel using 11 thread(s)
 Calc Triangle Approximation
 Object 0 has 882 triangles
 Calc Triangle Approximation
 Object 0 has 882 triangles


In [3]:
from netgen.meshing import MeshingStep

mesh = geo.GenerateMesh(maxh=0.4, perfstepsend=MeshingStep.MESHSURFACE) # no non-free dof
mesh = Mesh(mesh)
mesh.Curve(2)

Draw(mesh)

 Start Findpoints
 Analyze spec points
 Find edges
 Start Findpoints
 Analyze spec points
 Find edges
 Start Findpoints
 Analyze spec points
 Find edges
 Surface 1 / 1
 Optimize Surface
 Curve elements, order = 2


# FE Spaces

In [4]:
# func spaces

k = 1 # order
fes = H1(mesh, order=k)
fesV = VectorH1(mesh, order=k)

## Block matrix

In [5]:
from ngsolve.krylovspace import CG, GMRes

In [6]:
X = fesV.TrialFunction()
X_t = fesV.TestFunction() # _t for test func

# normal
n = GridFunction(fesV)
n.Set(specialcf.normal(3), definedon=mesh.Boundaries(".*"))

# bilinear form
tau = 1
a = BilinearForm(fesV)
a += InnerProduct(X,X_t)*ds(definedon = mesh.Boundaries('.*'))
a_mat = a.Assemble().mat

f1 = GridFunction(fes)
f2 = GridFunction(fesV)
f1.Set(1, definedon=mesh.Boundaries(".*"))
f2.Set(specialcf.normal(3), definedon=mesh.Boundaries(".*"))

id1 = IdentityMatrix(fes.ndof, complex=False)
id2 = IdentityMatrix(fesV.ndof, complex=False)

In [7]:
V = StokesSingleLayerPotentialOperatorij(fes, intorder=5, leafsize=20, eta=3, eps=1e-4, method="aca", testhmatrix=False, i=3, j=3)

In [8]:
rhs_vec = BlockVector([f2.vec,f2.components[0].vec,f2.components[1].vec,f2.components[2].vec])
V_mat = BlockMatrix([[V.mat,None,None],\
                     [None,V.mat,None],\
                     [None,None,V.mat]])
lhs_mat = BlockMatrix([[a_mat,None],\
                       [None,V_mat]])
pre = BlockMatrix([[id1,None],\
                   [None,id2]])

In [9]:
sol_sym = GMRes(A=lhs_mat, b=rhs_vec, pre=pre, tol=1e-8, maxsteps=400, printrates=False)

RuntimeError: std::bad_cast

# Manually solve FEM linear system

In [10]:
# solve the Poisson equation -Delta u = f
# with Dirichlet boundary condition u = 0

from ngsolve import *
# from netgen.geom2d import unit_square

ngsglobals.msg_level = 1

# generate a triangular mesh of mesh-size 0.2
mesh = Mesh(unit_square.GenerateMesh(maxh=0.4))

# H1-conforming finite element space
fes = H1(mesh, order=3, dirichlet=[1,2,3,4])

# define trial- and test-functions
u = fes.TrialFunction()
v = fes.TestFunction()

# the right hand side
f = LinearForm(fes)
f += 32 * (y*(1-y)+x*(1-x)) * v * dx

# the bilinear-form 
a = BilinearForm(fes, symmetric=True)
a += grad(u)*grad(v)*dx

a.Assemble()
f.Assemble()

# the solution field 
gfu = GridFunction(fes)
gfu.vec.data = a.mat.Inverse(fes.FreeDofs(), inverse="sparsecholesky") * f.vec
# print (u.vec)


# plot the solution (netgen-gui only)
Draw (gfu)
Draw (-grad(gfu), mesh, "Flux")

exact = 16*x*(1-x)*y*(1-y)
print ("L2-error:", sqrt (Integrate ( (gfu-exact)*(gfu-exact), mesh)))

L2-error: 0.0004940767110257937


In [11]:
print ("L2-error:", sqrt (Integrate ( (gfu)*(gfu), mesh)))

L2-error: 0.5333024378359452


In [12]:
(a.mat.Inverse(fes.FreeDofs(), inverse="sparsecholesky").ToDense().NumPy()).dot(f.vec.data.FV().NumPy())[1:10]\
-\
gfu.vec.data.FV().NumPy()[1:10]

array([0., 0., 0., 0., 0., 0., 0., 0., 0.])

### Therefore, .Inverse() is accurate

In [13]:
import numpy as np

a.mat.Inverse(fes.FreeDofs(), inverse="sparsecholesky").ToDense().NumPy()
-\
np.linalg.inv(a.mat.ToDense().NumPy())

array([[-1.39727761e+15, -1.39727761e+15, -1.39727761e+15, ...,
         5.88857814e-01,  5.40310345e+00,  1.68105854e+00],
       [-1.39727761e+15, -1.39727761e+15, -1.39727761e+15, ...,
         3.42390699e-01,  5.30474144e+00,  1.80228746e+00],
       [-1.39727761e+15, -1.39727761e+15, -1.39727761e+15, ...,
         3.60280621e-01,  5.28866348e+00,  1.79549852e+00],
       ...,
       [ 9.77030622e-01,  7.30563507e-01,  7.48453429e-01, ...,
        -1.41498687e+02, -6.43122451e+00, -2.22144584e+01],
       [ 4.14738137e+00,  4.04901936e+00,  4.03294139e+00, ...,
        -6.43122451e+00, -1.38193027e+02, -1.76563919e+01],
       [ 1.31111959e+00,  1.43234850e+00,  1.42555956e+00, ...,
        -2.22144584e+01, -1.76563919e+01, -1.38193027e+02]])

### not accurate???

In [14]:
np.linalg.cond(a.mat.ToDense().NumPy()),\
np.linalg.cond(a.mat.Inverse(fes.FreeDofs(), inverse="sparsecholesky").ToDense().NumPy())

(2.4874853815190624e+16, inf)

In [15]:
(a.mat.ToDense().NumPy()).dot(gfu.vec.data.FV().NumPy())[1:10]\
-\
f.vec.data.FV().NumPy()[1:10]

array([-0.49418982, -0.49405155, -0.49418982, -1.08643607, -1.08607853,
       -1.08626005, -1.08631732, -1.08643607, -1.08607853])

### not accurate???